In [1]:
from math import sqrt
import numpy as np

from funcoesTermosol import plota, importa, geraSaida

In [2]:
# gera saida 
# R -> matriz com as restrições 

nn,N,nm,Inc,nc,F,nr,R = importa("entrada.xlsx")

In [3]:
A = 2.25e-2    # m²
E = 210e9      # Pa | módulo de elasticidade
N_NODES = nn   # numero de nós

In [4]:
# Essa é a classe mais básica de todas. Ela é um ponto
# e possui propriedades de um ponto, como coordenada x,
# coordenada y.
class Point():
    def __init__(self, x:float, y:float):
        self.x = x
        self.y = y

    def __repr__(self):
        return f"({self.x}, {self.y})"
    
    # subtrarir p1 - p2 devolve um novo ponto (x2 - x1, y2 - y1)
    def __sub__(self, point):
        return Point(self.x - point.x, self.y - point.y)
    
    # somar p1 + p2 devolve um novo ponto (x1 + x2, y1 + y2)
    def __add__(self, point):
        return Point(self.x + point.x, self.y + point.y)

    # isso aqui serve para flexibilizar a sintaxe. Contextualmente,
    # não tem nada a ver com um ponto, então não se importe com isso
    def __iter__(self):
        yield self.x
        yield self.y
   
    # dividir p1 por um número n devolve um novo ponto (x1/n, y1/n)
    def __truediv__(self, number:int):
        return Point(self.x / number, self.y / number)
    
    # calcula a distância entre dois pontos (pitágoras das coordenadas)
    def dist(self, point) -> float:
        return sqrt( (self.x - point.x)**2 + (self.y - point.y)**2 )

In [5]:
# Essa classe representa um nó. Ela é um ponto (classe Point) com
# algumas características adicionais
class Node(Point):
    def __init__(self, x, y, value:int):
        super(Node, self).__init__(x, y)
        self.value = value # um ponto não tem a propriedade value, por exemplo
    
    # um ponto é representado apenas como tupla
    # um nó é representado como: "○ 1 (x, y)"
    def __repr__(self):
        return f"○ {self.value} ({self.x}, {self.y})"

# Essa classe representa um elemento. Ela possui 2 nós.
class Element():
    def __init__(self, node_1:Node, node_2:Node, value:int, E:float, A:float):
        self.value = value       # value de um elemento (elemento 1, elemento 2, ...)
        self.node_1 = node_1     # nó 1
        self.node_2 = node_2     # nó 2
        self.length = node_1.dist(node_2)  # comprimento do elemento
        self.cos, self.sin = self.slope()  # cos e sen do ângulo de inclinação
        
        self.m = np.array([[self.node_2.x - self.node_1.x], [self.node_2.y - self.node_1.y]])
        
        # self.S é a matriz de rigidez do elemento
        self.S = (E*A/self.length) * (self.m.dot(self.m.T)/(np.linalg.norm(self.m)**2))
        
    # inclinação
    def slope(self):
        cos, sin = (self.node_2 - self.node_1)/self.length
        return (cos, sin)
    
    def calc_strain(self, u1, v1, u2, v2):
        self.strain = np.array([ -self.cos, -self.sin, 
                                self.cos, self.sin ]).dot(np.array([[u1],[v1],[u2],[v2]]))/self.length
                                                                     
    @property
    def connectivity(self):
        connectivity_list = [0]*N_NODES
        connectivity_list[self.node_1.value - 1] = -1
        connectivity_list[self.node_2.value - 1] = 1
        return np.array( connectivity_list )

    def stiffness(self):
        c = np.array([self.connectivity])
        return np.kron(c.T.dot(c), self.S)
    
    def __repr__(self):
        return f"{self.node_1.value} ○--({self.value})--○ {self.node_2.value}"

In [18]:
class System():
    
    def __init__(self, E=E, A=A):
        self._E = E
        self._A = A
        self._nodes = []
        self._elements = []
        self._P = []
        self._loads = []
        self._constraints = []
        
    # Esse método adiciona 1 nó de coordenadas (x, y) ao sistema
    def add_node(self, x:float, y:float) -> None:
        new_node = Node(x, y, len(self._nodes) + 1)
        self._nodes.append( new_node )
        print(f"[SYS] created node: {new_node}")
    
    # Esse método adiciona restrições aos nós (x: direction = 1; y: direction = 2)
    def add_constraint(self, node:int, direction:int):
        self._constraints.append([node, direction])
        print(f"Constraints {'x' if direction == 1 else 'y'} added to node {node}")
        
    # adiciona uma carga a um dos nós do sistema (x: direction = 1; y: direction = 2)
    def add_load(self, node, direction, value):
        self._loads.append([node, direction, value])
        print(f"Load of {value} N ({'x' if direction == 1 else 'y'}) added to node {node}")
        
    # Esse método adiciona 1 elemento definido entre os nós n1 e n2
    def define_element(self, n1: int, n2: int, E=E, A=A):
        n1 = self._nodes[n1 - 1]
        n2 = self._nodes[n2 - 1]
        new_element = Element(n1, n2, value=len(self._elements) + 1, E=self._E, A=self._A)
        self._elements.append( new_element )
        print(f"[SYS] created element: {new_element}")
    
    # Esse método retorna um nó. Uso: 
    # system.node(1) retorna o nó 1
    # Se 3 nós foram adicionados, eles são númerados como 
    # 1, 2 e 3, então não se preocupe com índices a partir do 0
    def node(self, number:int) -> Node:
        return self._nodes[number - 1]
    
    @property
    def nodes(self):
        return np.array([ [n.x, n.y] for n in self._nodes ]).T

    # análogo ao anterior. system.element(1) retorna o elemento 1
    def element(self, number:int) -> Element:
        return self._elements[number - 1]
    
    # devolve a matriz dos nós
    @property
    def N(self):
        return np.array([ [n.x for n in self._nodes], [n.y for n in self._nodes] ])
    
    # devolve a matriz de conectividade
    @property
    def C(self):
        return np.array( [el.connectivity for el in self._elements] )
   
    # devolve a matriz 
    @property
    def K(self):
        return sum( [el.stiffness() for el in self._elements] )
    
    @property
    def strain(self):
        return np.array( [el.strain for el in self._elements] )
    
    def jacobi(self, F):
        P = F.copy()
        K = self.K.copy()

        deleted_positions = []
        
        for node, direction in self._constraints:
            P = np.delete(P, 2*(int(node) - 1) + int(direction)//2, 0)
            K = np.delete(K, 2*(int(node) - 1) + int(direction)//2, 0)
            K = np.delete(K, 2*(int(node) - 1) + int(direction)//2, 1)
            deleted_positions.append( 2*(int(node) - 1) + int(direction)//2 )
              
        # Create an initial guess if needed                                                                                                                                                            
        x = np.zeros((P.shape[0], 1))

        # Create a vector of the diagonal elements of A                                                                                                                                                
        # and subtract them from A                                                                                                                                                                     
        D = np.diag(K)
#         D =  [1.11205398e+10 9.45000000e+09 1.11205398e+10 8.06607954e+09
#                  8.06607954e+09 3.34107954e+09 8.06607954e+09 8.06607954e+09
#                  8.06607954e+09 1.27910795e+10 1.27910795e+10]

        R = K - np.diagflat(D)
        
        old_x = x.copy()
        done = False
        while not done:
            x = np.nan_to_num((P - R.dot(x)) / D)
             
            x = np.diag(x)
            print("x {}".format(x))
            delta_x = x - old_x
            old_x = x.copy()
            
#             error = np.nan_to_num(delta_x[np.abs(x) >= 1e-6]/x[np.abs(x) >= 1e-6])
#             print("error {}".format(error))  

            if np.max(np.abs(delta_x)) < 1e-8:
                done = True
              
        U = np.zeros( (2*len(self._nodes), 1) )

        counter = 0
        for i in range(2*len(self._nodes)):
            if (i not in deleted_positions):
                U[i] = x[counter]
                counter += 1
        
        R = self.K.dot(U)
        R[np.abs(R) < 1e-7] = 0
        
        for el in self._elements:
            values = U[ [2*(el.node_1.value - 1), 2*(el.node_1.value - 1) + 1, 
                         2*(el.node_2.value - 1), 2*(el.node_2.value - 1) + 1] , 0]
            el.calc_strain(*values)
        return R, self.strain, U 
                              
    # usa linalg para resolver o sistema          
    def solve(self, F):
        P = F.copy()
        K = self.K.copy()

        deleted_positions = []
        
        for node, direction in self._constraints:
            P = np.delete(P, 2*(int(node) - 1) + int(direction)//2, 0)
            K = np.delete(K, 2*(int(node) - 1) + int(direction)//2, 0)
            K = np.delete(K, 2*(int(node) - 1) + int(direction)//2, 1)
            deleted_positions.append( 2*(int(node) - 1) + int(direction)//2 )
        
        solve = np.linalg.solve(K, P)
        
        U = np.zeros( (2*len(self._nodes), 1) )
        
        counter = 0
        for i in range(2*len(self._nodes)):
            if (i not in deleted_positions):
                U[i] = solve[counter]
                counter += 1
        
        R = self.K.dot(U)
        R[np.abs(R) < 1e-7] = 0
        
        for el in self._elements:
            values = U[ [2*(el.node_1.value - 1), 2*(el.node_1.value - 1) + 1, 
                         2*(el.node_2.value - 1), 2*(el.node_2.value - 1) + 1] , 0]
            el.calc_strain(*values)
        
        return R, self.strain, U

In [19]:
system = System()

for x, y in N.T:
    system.add_node(int(x), int(y))
    
for x, y, elasticity, area in Inc:
    system.define_element(int(x), int(y), elasticity, area)

[SYS] created node: ○ 1 (0, 0)
[SYS] created node: ○ 2 (1, 0)
[SYS] created node: ○ 3 (2, 0)
[SYS] created node: ○ 4 (3, 0)
[SYS] created node: ○ 5 (4, 0)
[SYS] created node: ○ 6 (3, 1)
[SYS] created node: ○ 7 (2, 2)
[SYS] created node: ○ 8 (1, 1)
[SYS] created node: ○ 9 (2, 1)
[SYS] created element: 1 ○--(1)--○ 2
[SYS] created element: 2 ○--(2)--○ 3
[SYS] created element: 3 ○--(3)--○ 4
[SYS] created element: 4 ○--(4)--○ 5
[SYS] created element: 5 ○--(5)--○ 6
[SYS] created element: 6 ○--(6)--○ 7
[SYS] created element: 7 ○--(7)--○ 8
[SYS] created element: 8 ○--(8)--○ 1
[SYS] created element: 2 ○--(9)--○ 8
[SYS] created element: 2 ○--(10)--○ 9
[SYS] created element: 3 ○--(11)--○ 9
[SYS] created element: 9 ○--(12)--○ 4
[SYS] created element: 4 ○--(13)--○ 6
[SYS] created element: 9 ○--(14)--○ 6
[SYS] created element: 8 ○--(15)--○ 9
[SYS] created element: 9 ○--(16)--○ 7


In [20]:
print("Matriz de nós:")
print(system.N)

Matriz de nós:
[[0 1 2 3 4 3 2 1 2]
 [0 0 0 0 0 1 2 1 1]]


In [21]:
print("Matriz de conectividade:")
print(system.C.T)

Matriz de conectividade:
[[-1  0  0  0  0  0  0  1  0  0  0  0  0  0  0  0]
 [ 1 -1  0  0  0  0  0  0 -1 -1  0  0  0  0  0  0]
 [ 0  1 -1  0  0  0  0  0  0  0 -1  0  0  0  0  0]
 [ 0  0  1 -1  0  0  0  0  0  0  0  1 -1  0  0  0]
 [ 0  0  0  1 -1  0  0  0  0  0  0  0  0  0  0  0]
 [ 0  0  0  0  1 -1  0  0  0  0  0  0  1  1  0  0]
 [ 0  0  0  0  0  1 -1  0  0  0  0  0  0  0  0  1]
 [ 0  0  0  0  0  0  1 -1  1  0  0  0  0  0 -1  0]
 [ 0  0  0  0  0  0  0  0  0  1  1 -1  0 -1  1 -1]]


In [22]:
F;

In [23]:
CONSTRAINTS = R

i = range(CONSTRAINTS.shape[0] - 1, -1, -1)
new = CONSTRAINTS[i,:]
new;

In [24]:
for node, direction in new:
    system.add_constraint(node, direction)

ValueError: not enough values to unpack (expected 2, got 1)

In [25]:
# R, strain, U = system.solve(F)
R, strain, U = system.jacobi(F)

# Reacoes de apoio [N]
R;

x [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
  0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
  0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
  5.98608915e-07 -1.23975966e-06  2.47951931e-07  0.00000000e+00
  0.00000000e+00  0.00000000e+00]
x [ 6.47660053e-08  2.47951931e-07  0.00000000e+00  0.00000000e+00
  0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
  0.00000000e+00  0.00000000e+00  3.80738598e-07 -3.80738598e-07
  7.22584881e-07 -1.18840713e-06  1.15165265e-07 -2.35491719e-07
  9.15929630e-08 -4.57964815e-07]
x [-9.61957413e-08 -1.85092459e-07 -2.75183922e-08 -2.69678117e-07
  0.00000000e+00 -4.57964815e-07  8.25551766e-08 -4.24834822e-07
  1.98900794e-07 -7.61477195e-07  2.91726229e-07 -2.38072313e-07
  9.19184286e-07 -1.69065675e-06  3.67440769e-07 -7.94119560e-08
  1.83185926e-07 -4.38995291e-07]
x [ 1.03250628e-07  3.84224555e-07 -3.87891762e-08 -1.18299732e-07
  2.75183922e-08 -4.38995291e-07  1.14156442e

x [ 1.76507932e+79  4.01420013e+79 -6.58884636e+78  7.22347018e+78
  4.39490124e+78  1.04351851e+62 -6.58884636e+78 -7.22347018e+78
  1.76507932e+79 -4.01420013e+79 -2.17858298e+79  2.07443607e+79
  2.83685453e+79  1.29232228e+62 -2.17858298e+79 -2.07443607e+79
  1.06253303e+79  2.68560094e+62]
x [-2.64621110e+79 -6.01809836e+79  9.87801410e+78 -1.08294436e+79
 -6.58884636e+78  2.68560094e+62  9.87801410e+78  1.08294436e+79
 -2.64621110e+79  6.01809836e+79  3.26613677e+79 -3.10999948e+79
 -4.25301904e+79 -4.15801937e+62  3.26613677e+79  3.10999948e+79
 -1.59295204e+79 -2.25529939e+62]
x [ 3.96720596e+79  9.02234734e+79 -1.48091422e+79  1.62355276e+79
  9.87801410e+78 -2.25529939e+62 -1.48091422e+79 -1.62355276e+79
  3.96720596e+79 -9.02234734e+79 -4.89659999e+79  4.66251860e+79
  6.37613624e+79  2.43721324e+62 -4.89659999e+79 -4.66251860e+79
  2.38815748e+79 -4.55950921e+61]
x [-5.94764459e+79 -1.35263245e+80  2.22019011e+79 -2.43403415e+79
 -1.48091422e+79 -4.55950921e+61  2.22019011e

x [-4.53320890e+147 -1.03095694e+148  1.69219687e+147 -1.85518571e+147
 -1.12873145e+147  1.34472904e+130  1.69219687e+147  1.85518571e+147
 -4.53320890e+147  1.03095694e+148  5.59519997e+147 -5.32772208e+147
 -7.28582228e+147 -3.97680717e+130  5.59519997e+147  5.32772208e+147
 -2.72887691e+147 -4.89405485e+129]
x [ 6.79619754e+147  1.54561309e+148 -2.53694557e+147  2.78129883e+147
  1.69219687e+147 -4.89405485e+129 -2.53694557e+147 -2.78129883e+147
  6.79619754e+147 -1.54561309e+148 -8.38833707e+147  7.98733359e+147
  1.09229220e+148 -5.45142764e+129 -8.38833707e+147 -7.98733359e+147
  4.09113874e+147 -9.50117279e+130]
x [-1.01888755e+148 -2.31718682e+148  3.80339481e+147 -4.16972980e+147
 -2.53694557e+147 -9.50117279e+130  3.80339481e+147  4.16972980e+147
 -1.01888755e+148  2.31718682e+148  1.25758148e+148 -1.19746295e+148
 -1.63756707e+148  1.57856554e+131  1.25758148e+148  1.19746295e+148
 -6.13344490e+147 -1.61034864e+130]
x [ 1.52751863e+148  3.47393198e+148 -5.70205853e+147  6.2

x [ 4.01794129e+213  9.13773126e+213 -1.49985316e+213  1.64431586e+213
  1.00043409e+213 -1.69039701e+196 -1.49985316e+213 -1.64431586e+213
  4.01794129e+213 -9.13773126e+213 -4.95922104e+213  4.72214605e+213
  6.45767861e+213  3.25670469e+195 -4.95922104e+213 -4.72214605e+213
  2.41869886e+213 -1.56393107e+196]
x [-6.02370711e+213 -1.36993084e+214  2.24858341e+213 -2.46516224e+213
 -1.49985316e+213 -1.56393107e+196  2.24858341e+213  2.46516224e+213
 -6.02370711e+213  1.36993084e+214  7.43487596e+213 -7.07945257e+213
 -9.68136710e+213 -1.52375542e+197  7.43487596e+213  7.07945257e+213
 -3.62611907e+213 -3.10867954e+196]
x [ 9.03075600e+213  2.05380356e+214 -3.37108159e+213  3.69577707e+213
  2.24858341e+213 -3.10867954e+196 -3.37108159e+213 -3.69577707e+213
  9.03075600e+213 -2.05380356e+214 -1.11463837e+214  1.06135321e+214
  1.45143285e+214 -5.05911536e+197 -1.11463837e+214 -1.06135321e+214
  5.43628632e+213 -6.70858161e+196]
x [-1.35389308e+214 -3.07906718e+214  5.05393351e+213 -5.5

  1.23898489e+297  3.75201441e+280]
x [-3.08565990e+297 -7.01750695e+297  1.15184280e+297 -1.26278587e+297
 -7.68303745e+296  3.75201441e+280  1.15184280e+297  1.26278587e+297
 -3.08565990e+297  7.01750695e+297  3.80853487e+297 -3.62646830e+297
 -4.95930590e+297  1.12802869e+281  3.80853487e+297  3.62646830e+297
 -1.85748908e+297 -2.07020468e+280]
x [ 4.62602864e+297  1.05206631e+298 -1.72684546e+297  1.89317158e+297
  1.15184280e+297 -2.07020468e+280 -1.72684546e+297 -1.89317158e+297
  4.62602864e+297 -1.05206631e+298 -5.70976451e+297  5.43680988e+297
  7.43500317e+297  1.77761154e+281 -5.70976451e+297 -5.43680988e+297
  2.78475204e+297  1.00352998e+281]
x [-6.93535311e+297 -1.57726030e+298  2.58889081e+297 -2.83824732e+297
 -1.72684546e+297  1.00352998e+281  2.58889081e+297  2.83824732e+297
 -6.93535311e+297  1.57726030e+298  8.56009250e+297 -8.15087827e+297
 -1.11465744e+298  5.18414171e+280  8.56009250e+297  8.15087827e+297
 -4.17490687e+297  7.31094936e+280]
x [ 1.03974978e+298  2

...

x [ 1.79769313e+308  1.79769313e+308  0.00000000e+000  0.00000000e+000
  1.79769313e+308  1.79769313e+308 -1.79769313e+308  1.79769313e+308
  1.79769313e+308 -1.79769313e+308  0.00000000e+000  0.00000000e+000
  1.79769313e+308  1.79769313e+308 -1.79769313e+308 -1.79769313e+308
  1.79769313e+308 -1.79769313e+308]
x [-1.79769313e+308 -1.79769313e+308  0.00000000e+000  0.00000000e+000
 -1.79769313e+308 -1.79769313e+308  1.79769313e+308 -1.79769313e+308
 -1.79769313e+308  1.79769313e+308  0.00000000e+000  0.00000000e+000
 -1.79769313e+308 -1.79769313e+308  1.79769313e+308  1.79769313e+308
 -1.79769313e+308  1.79769313e+308]
x [ 1.79769313e+308  1.79769313e+308  0.00000000e+000  0.00000000e+000
  1.79769313e+308  1.79769313e+308 -1.79769313e+308  1.79769313e+308
  1.79769313e+308 -1.79769313e+308  0.00000000e+000  0.00000000e+000
  1.79769313e+308  1.79769313e+308 -1.79769313e+308 -1.79769313e+308
  1.79769313e+308 -1.79769313e+308]
x [-1.79769313e+308 -1.79769313e+308  0.00000000e+000  0.0

 -1.79769313e+308  1.79769313e+308]
x [ 1.79769313e+308  1.79769313e+308  0.00000000e+000  0.00000000e+000
  1.79769313e+308  1.79769313e+308 -1.79769313e+308  1.79769313e+308
  1.79769313e+308 -1.79769313e+308  0.00000000e+000  0.00000000e+000
  1.79769313e+308  1.79769313e+308 -1.79769313e+308 -1.79769313e+308
  1.79769313e+308 -1.79769313e+308]
x [-1.79769313e+308 -1.79769313e+308  0.00000000e+000  0.00000000e+000
 -1.79769313e+308 -1.79769313e+308  1.79769313e+308 -1.79769313e+308
 -1.79769313e+308  1.79769313e+308  0.00000000e+000  0.00000000e+000
 -1.79769313e+308 -1.79769313e+308  1.79769313e+308  1.79769313e+308
 -1.79769313e+308  1.79769313e+308]
x [ 1.79769313e+308  1.79769313e+308  0.00000000e+000  0.00000000e+000
  1.79769313e+308  1.79769313e+308 -1.79769313e+308  1.79769313e+308
  1.79769313e+308 -1.79769313e+308  0.00000000e+000  0.00000000e+000
  1.79769313e+308  1.79769313e+308 -1.79769313e+308 -1.79769313e+308
  1.79769313e+308 -1.79769313e+308]
x [-1.79769313e+308 -1

x [ 1.79769313e+308  1.79769313e+308  0.00000000e+000  0.00000000e+000
  1.79769313e+308  1.79769313e+308 -1.79769313e+308  1.79769313e+308
  1.79769313e+308 -1.79769313e+308  0.00000000e+000  0.00000000e+000
  1.79769313e+308  1.79769313e+308 -1.79769313e+308 -1.79769313e+308
  1.79769313e+308 -1.79769313e+308]
x [-1.79769313e+308 -1.79769313e+308  0.00000000e+000  0.00000000e+000
 -1.79769313e+308 -1.79769313e+308  1.79769313e+308 -1.79769313e+308
 -1.79769313e+308  1.79769313e+308  0.00000000e+000  0.00000000e+000
 -1.79769313e+308 -1.79769313e+308  1.79769313e+308  1.79769313e+308
 -1.79769313e+308  1.79769313e+308]
x [ 1.79769313e+308  1.79769313e+308  0.00000000e+000  0.00000000e+000
  1.79769313e+308  1.79769313e+308 -1.79769313e+308  1.79769313e+308
  1.79769313e+308 -1.79769313e+308  0.00000000e+000  0.00000000e+000
  1.79769313e+308  1.79769313e+308 -1.79769313e+308 -1.79769313e+308
  1.79769313e+308 -1.79769313e+308]
x [-1.79769313e+308 -1.79769313e+308  0.00000000e+000  0.0

x [-1.79769313e+308 -1.79769313e+308  0.00000000e+000  0.00000000e+000
 -1.79769313e+308 -1.79769313e+308  1.79769313e+308 -1.79769313e+308
 -1.79769313e+308  1.79769313e+308  0.00000000e+000  0.00000000e+000
 -1.79769313e+308 -1.79769313e+308  1.79769313e+308  1.79769313e+308
 -1.79769313e+308  1.79769313e+308]
x [ 1.79769313e+308  1.79769313e+308  0.00000000e+000  0.00000000e+000
  1.79769313e+308  1.79769313e+308 -1.79769313e+308  1.79769313e+308
  1.79769313e+308 -1.79769313e+308  0.00000000e+000  0.00000000e+000
  1.79769313e+308  1.79769313e+308 -1.79769313e+308 -1.79769313e+308
  1.79769313e+308 -1.79769313e+308]
x [-1.79769313e+308 -1.79769313e+308  0.00000000e+000  0.00000000e+000
 -1.79769313e+308 -1.79769313e+308  1.79769313e+308 -1.79769313e+308
 -1.79769313e+308  1.79769313e+308  0.00000000e+000  0.00000000e+000
 -1.79769313e+308 -1.79769313e+308  1.79769313e+308  1.79769313e+308
 -1.79769313e+308  1.79769313e+308]
x [ 1.79769313e+308  1.79769313e+308  0.00000000e+000  0.0

KeyboardInterrupt: 

In [16]:
R

array([[ -467.68667686],
       [ -391.96513575],
       [   67.37445649],
       [ 1984.91347077],
       [ -156.76330788],
       [ 3369.68597974],
       [   11.93866369],
       [ 3249.74472886],
       [-3013.26952621],
       [ 1948.70616692],
       [  455.86370407],
       [ -485.00519104],
       [ 1631.53051728],
       [-9803.28722427],
       [ 2242.03925956],
       [  271.23176434],
       [ -771.02709013],
       [ -144.02455956]])

In [17]:
# Deslocamento [m]
U

array([[ 0.00000000e+00],
       [ 0.00000000e+00],
       [ 1.60257230e-08],
       [ 0.00000000e+00],
       [ 1.04076359e-07],
       [ 0.00000000e+00],
       [ 2.25304415e-07],
       [ 0.00000000e+00],
       [ 0.00000000e+00],
       [ 0.00000000e+00],
       [ 8.22741992e-07],
       [-3.43770893e-07],
       [ 1.18889771e-06],
       [-1.82613055e-06],
       [ 5.68437275e-07],
       [-3.33803450e-07],
       [ 4.85138609e-07],
       [-7.13161054e-07]])

In [ ]:
# desformaçao [ ]
strain

In [ ]:
# Tensoes internas [Pa]
stress_element = E*strain
stress_element ;

In [ ]:
# Forças internas [N]
Fi = A*stress_element
Fi;

####  Gráfico de saída 

In [ ]:
# geraSaida(nome,Ft,Ut,Epsi,Fi,Ti)
geraSaida("saida", R, U, strain, Fi, stress_element)

In [ ]:
# plotar o grafico de entrada e de saida 
# def plota(N,Inc)

# ENTRADA 
plota(N, Inc)

In [ ]:
n = system.nodes
n = n.astype("float64")
n

In [ ]:
for index, linha in enumerate(U):
    n[index%2, index//2] = n[index%2, index//2] + linha*2e5

In [ ]:
plota(n, Inc)